## Libraries

In [2]:
# Essentials
import torch
import torch.nn as nn
from torch.utils.data import DataLoader, TensorDataset
from torchvision import datasets, transforms
import matplotlib.pyplot as plt
from matplotlib.colors import TwoSlopeNorm, ListedColormap
from matplotlib.patches import Ellipse
from matplotlib.gridspec import GridSpec, GridSpecFromSubplotSpec
from skbio.stats.ordination import pcoa
from skbio.stats.distance import DistanceMatrix, permanova
from sklearn.mixture import GaussianMixture
from sklearn.metrics import adjusted_rand_score
import scipy.stats as stats
from scipy.stats import spearmanr
from scipy.spatial.distance import pdist, squareform
from scipy.stats import mannwhitneyu, kruskal, nbinom, multivariate_normal
from statsmodels.stats.multitest import multipletests
from mpl_toolkits.axes_grid1 import make_axes_locatable
import numpy as np
import pandas as pd
import os
import re
import random
import statsmodels.api as sm
import seaborn as sns
import networkx as nx
# User libraries
from src.ABaCo.BatchEffectDataLoader import DataPreprocess, DataTransform, one_hot_encoding
from src.ABaCo.BatchEffectCorrection import correctCombat, correctLimma_rBE, correctBMC, correctPLSDAbatch_R, correctCombatSeq, correctConQuR
from src.ABaCo.BatchEffectPlots import plotPCA, plotPCoA, plot_LISI_perplexity
from src.ABaCo.BatchEffectMetrics import all_metrics, pairwise_distance, pairwise_distance_std, PERMANOVA, pairwise_distance_multi_run, kBET, ARI, ASW, iLISI_norm
from src.ABaCo.ABaCo import abaco_run, abaco_recon, contour_plot, abaco_run_ensemble, abaco_recon_ensemble

>> clustergrammer2 backend version 0.18.0


## Data loading

### Original datasets

In [2]:
# Load AD count
path = "data/dataset_ad.csv"
ad_count_batch_label = "batch"
ad_count_sample_label = "sample"
ad_count_bio_label = "trt"

ad_count_data = DataPreprocess(
    path,
    factors=[ad_count_sample_label, ad_count_batch_label, ad_count_bio_label]
)

# train DataLoader: [samples, ohe_batch]
ad_count_input_size = 567
ad_count_train_dataloader = DataLoader(
    TensorDataset(
        torch.tensor(ad_count_data.select_dtypes(include="number").values, dtype=torch.float32), # samples
        one_hot_encoding(ad_count_data[ad_count_batch_label])[0], # one hot encoded batch information
        one_hot_encoding(ad_count_data[ad_count_bio_label])[0], #one hot encoded biological information
    ),
    batch_size=1000,
)
ad_count_batch_size = 5
ad_count_bio_size = 2

# Load IBD data
path = "data/MGnify/IBD/IBD_dataset_genus.csv"
ibd_batch_label = "project ID"
ibd_sample_label = "run ID"
ibd_bio_label = "associated phenotype"

ibd_data = DataPreprocess(
    path,
    factors=[ibd_sample_label, ibd_batch_label, ibd_bio_label]
)

# train DataLoader: [samples, ohe_batch]
ibd_input_size = 193
ibd_train_dataloader = DataLoader(
    TensorDataset(
        torch.tensor(ibd_data.select_dtypes(include="number").values, dtype=torch.float32), # samples
        one_hot_encoding(ibd_data[ibd_batch_label])[0], # one hot encoded batch information
        one_hot_encoding(ibd_data[ibd_bio_label])[0], #one hot encoded biological information
    ),
    batch_size=1000,
)
ibd_batch_size = 2
ibd_bio_size = 3

# Load DTU-GE data
path = "data/MGnify/DTU-GE/count/DTU-GE_phylum_count_data_filtered.csv"
dtu_batch_label = "pipeline"
dtu_sample_label = "accession"
dtu_bio_label = "location"

dtu_data = DataPreprocess(
    path,
    factors=[dtu_sample_label, dtu_batch_label, dtu_bio_label]
)

# train DataLoader: [samples, ohe_batch]
dtu_input_size = 162
dtu_train_dataloader = DataLoader(
    TensorDataset(
        torch.tensor(dtu_data.select_dtypes(include="number").values, dtype=torch.float32), # samples
        one_hot_encoding(dtu_data[dtu_batch_label])[0], # one hot encoded batch information
        one_hot_encoding(dtu_data[dtu_bio_label])[0], #one hot encoded biological information
    ),
    batch_size=1000,
)
dtu_batch_size = 2
dtu_bio_size = 4

ad_count_data_clr = DataTransform(data = ad_count_data, factors=[ad_count_sample_label, ad_count_batch_label, ad_count_bio_label], transformation="CLR", count=True)
ibd_data_clr = DataTransform(data = ibd_data, factors=[ibd_sample_label, ibd_batch_label, ibd_bio_label], transformation="CLR", count=True)
dtu_data_clr = DataTransform(data = dtu_data, factors=[dtu_sample_label, dtu_batch_label, dtu_bio_label], transformation="CLR", count=True)

### ABaCo runs

In [3]:
datasets = ["AD_count", "IBD", "DTU-GE"]
dataset_labels = ["AD count", "IBD", "DTU-GE"]
priors = ["vmm_kl", "mog_kl", "std_kl", "vmm_no", "mog_no", "std_no"]
prior_labels = ["VMM w/ KL cycle", "MoG w/ KL cycle", "Std w/ KL cycle", "VMM w/o KL cycle", "MoG w/o KL cycle", "Std w/o KL cycle"]
mult = 1
bio_label = ["trt", "associated phenotype", "location"]
sample_label = ["sample", "run ID", "accession"]
batch_label = ["batch", "project ID", "pipeline"]

multi_runs = []

for j, dataset in enumerate(datasets):
    folder = f"performance_metrics/multi_runs/{dataset}"

    for k, prior in enumerate(priors):
        if (dataset == "DTU-GE"):
            if (prior == "vmm_kl") | (prior == "vmm_no"):
                file_paths = [os.path.join(folder, file) 
                                for file in os.listdir(folder) 
                                if file.startswith(prior) and 
                                os.path.isfile(os.path.join(folder, file)) and
                                int(re.search(r"\d+$", file).group()) % mult == 0 and
                                re.search(r"kl_annealing_\d+$", os.path.splitext(file)[0])]
                
            else:
                file_paths = [os.path.join(folder, file) 
                                for file in os.listdir(folder) 
                                if file.startswith(prior) and 
                                os.path.isfile(os.path.join(folder, file)) and
                                int(re.search(r"\d+$", file).group()) % mult == 0 and
                                re.search(r"contra_1000_\d+$", os.path.splitext(file)[0])]
            
        elif (dataset == "IBD"):
            if (prior == "vmm_kl") | (prior == "vmm_no"):
                file_paths = [os.path.join(folder, file) 
                                for file in os.listdir(folder) 
                                if file.startswith(prior) and 
                                os.path.isfile(os.path.join(folder, file)) and
                                int(re.search(r"\d+$", file).group()) % mult == 0 and
                                re.search(r"kl_annealing_\d+$", os.path.splitext(file)[0])]
                
            else:
                file_paths = [os.path.join(folder, file) 
                                for file in os.listdir(folder) 
                                if file.startswith(prior) and 
                                os.path.isfile(os.path.join(folder, file)) and
                                int(re.search(r"\d+$", file).group()) % mult == 0 and
                                re.search(r"contra_1000_2_\d+$", os.path.splitext(file)[0])]

        else:
            file_paths = [os.path.join(folder, file) 
                            for file in os.listdir(folder) 
                            if file.startswith(prior) and 
                            os.path.isfile(os.path.join(folder, file)) and
                            int(re.search(r"\d+$", file).group()) % mult == 0]

        for i, file in enumerate(file_paths):
            run = DataPreprocess(path = file, factors = [sample_label[j], batch_label[j], bio_label[j]])
            run_format = {
                "iter":i,
                "dataset": dataset,
                "run": run,
                "prior": prior,
                "path":file,
            }
            multi_runs.append(run_format)

multi_runs = pd.DataFrame(multi_runs)

## 1. Robustness in differentially regulated taxa

### Define Kruskal-wallis test

In [5]:
# Define function to compute Kruskal-Wallis per taxa
def kruskal_wallis_taxa(df, sample_label, batch_label, bio_label, method):
    # Melt dataframe
    melt_df = pd.melt(df, id_vars = [sample_label, batch_label, bio_label], var_name = "taxa", value_name = "norm_counts")
    # Comput K-W test
    results = []
    # Per taxa
    for taxon, df_taxa in melt_df.groupby("taxa"):
        # For each biological group
        groups = []

        for grp, df_grp in df_taxa.groupby(bio_label):

            groups.append(df_grp["norm_counts"].values)

        try:
            stat, pval = kruskal(*groups)
            
        except ValueError:
            continue

        results.append({"taxa":taxon,
                        "H_stat":stat,
                        "p-value":pval})

    kw_df = pd.DataFrame(results)

    rej, p_adj, _, _ = multipletests(kw_df["p-value"], method = "fdr_bh")
    kw_df["p_adj"] = p_adj
    kw_df["significant"] = rej
    kw_df["method"] = method
    return kw_df

### Kruskal-wallis on all runs

In [6]:
priors = ["vmm_no", "vmm_kl", "std_no", "std_kl"]
prior_labels = ["ABaCo", "ABaCo (w/ KL cycle)"]
dataset_labels = ["Anaerobic digestion dataset", "IBD dataset", "DTU-GE dataset"]

# Original
ad_taxa_cols = ad_count_data_clr.select_dtypes(include = "number").columns
ad_non_num_cols = ad_count_data_clr.select_dtypes(exclude = "number").columns

ibd_taxa_cols = ibd_data_clr.select_dtypes(include = "number").columns
ibd_non_num_cols = ibd_data_clr.select_dtypes(exclude = "number").columns

dtu_taxa_cols = dtu_data_clr.select_dtypes(include = "number").columns
dtu_non_num_cols = dtu_data_clr.select_dtypes(exclude = "number").columns

non_num_cols = [ad_non_num_cols, ibd_non_num_cols, dtu_non_num_cols]
taxa_cols = [ad_taxa_cols, ibd_taxa_cols, dtu_taxa_cols]

robust_results = pd.DataFrame()

for i, dataset in enumerate(datasets):

    for j, prior in enumerate(priors):

        if (dataset == "AD_count") & ((prior == "vmm_no") | (prior == "vmm_kl")):

            print(dataset)
            print(prior)

            abaco_runs = multi_runs[(multi_runs["dataset"] == dataset) & (multi_runs["prior"] == prior)]
            
            kw_results_abaco = pd.DataFrame()

            for k, abaco_run in enumerate(abaco_runs["run"]):

                recon_data = DataTransform(abaco_run, factors = [sample_label[i], batch_label[i], bio_label[i]], count = True)

                top_taxa_abaco_data = recon_data[list(non_num_cols[i]) + list(taxa_cols[i])]
                kw_results_abaco = pd.concat([kw_results_abaco, kruskal_wallis_taxa(top_taxa_abaco_data, sample_label[i], batch_label[i], bio_label[i], k)], axis = 0)
            
            kw_results_abaco["dataset"] = dataset
            kw_results_abaco["prior"] = prior

            robust_results = pd.concat([robust_results, kw_results_abaco], axis = 0)
        
        elif ((dataset == "IBD") | (dataset == "DTU-GE")) & ((prior == "std_no") | (prior == "std_kl")):

            print(dataset)
            print(prior)

            abaco_runs = multi_runs[(multi_runs["dataset"] == dataset) & (multi_runs["prior"] == prior)]
            
            kw_results_abaco = pd.DataFrame()

            for k, abaco_run in enumerate(abaco_runs["run"]):

                recon_data = DataTransform(abaco_run, factors = [sample_label[i], batch_label[i], bio_label[i]], count = True)

                top_taxa_abaco_data = recon_data[list(non_num_cols[i]) + list(taxa_cols[i])]
                kw_results_abaco = pd.concat([kw_results_abaco, kruskal_wallis_taxa(top_taxa_abaco_data, sample_label[i], batch_label[i], bio_label[i], k)], axis = 0)
            
            kw_results_abaco["dataset"] = dataset
            kw_results_abaco["prior"] = prior

            robust_results = pd.concat([robust_results, kw_results_abaco], axis = 0)

AD_count
vmm_no
AD_count
vmm_kl
IBD
std_no
IBD
std_kl
DTU-GE
std_no
DTU-GE
std_kl


### Filtering only taxonomic groups that appeared at least once as significant

In [7]:
new_df = pd.DataFrame()

for j, taxa in enumerate(robust_results["taxa"].unique()):
    for i, prior in enumerate(robust_results["prior"].unique()):
        selected = robust_results[(robust_results["taxa"] == taxa) & (robust_results["prior"] == prior)]
        if selected["significant"].sum() > 0:
            new_df = pd.concat([new_df, selected], axis = 0)

### Plotting heat map

In [19]:
# Select DataFrame dataset and prior
dataset = "DTU-GE"
prior = "std_kl"
df = new_df[(new_df["dataset"] == dataset) & (new_df["prior"]==prior)]

# Pivot the DataFrame
pvals = df.pivot(index='taxa', columns='method', values='p_adj')
sig = df.pivot(index='taxa', columns='method', values='significant').astype(int)  # True->1, False->0

# Create a two-color colormap: blue for 0, red for 1
cmap = ListedColormap(['blue', 'red'])

# Plot
fig, ax = plt.subplots(figsize=(40, 70))
im = ax.imshow(sig, cmap=cmap, aspect='auto')

# Set ticks
ax.set_xticks(range(len(pvals.columns)))
ax.set_xticklabels(pvals.columns, rotation=45, ha='right')
ax.set_yticks(range(len(pvals.index)))
ax.set_yticklabels(pvals.index)

# Annotate with p_adj values
for i in range(sig.shape[0]):
    for j in range(sig.shape[1]):
        text = f"{pvals.iloc[i, j]:.3f}"
        ax.text(j, i, text, ha='center', va='center', color='white' if sig.iloc[i, j] else 'black')

ax.set_xlabel('method')
ax.set_ylabel('taxa')
ax.set_title('Heatmap of Adjusted p-values with Significance')
plt.grid(False)
plt.tight_layout()
plt.show()

pvals.to_excel(f"robustness_{dataset}_abaco_{prior}.xlsx", index=True)

## 2. Simulated data (balanced)

The following simulated data correction are going to be performed:
- Batch correction on data without batch effect (with significant different biological groups)
- Batch correction on data without batch effect (without significant different biological groups)
- Correction on data with batch effect (with significant different biological groups)
- Correction on data with batch effect (without significant different biological groups)

#### Creating simulated datasets

In [3]:
# Define random seed
np.random.seed(42)

n_samples = 75
n_features = 100
p_diff = 0.8
b_diff = 0.5

n_diff = int(n_features * p_diff)
b_diff = int(n_features * b_diff)

batches = ["Batch 1", "Batch 2"]
bios = ["A", "B"]

# Start several simulation data
sims = 50
sim_data_no_bt = []
sim_data_no_b = []
sim_data_no_t = []
sim_data_bt = []

for i in range(sims):

    # Build metadata
    metadata = pd.DataFrame({
        "SampleID": [f"S{i+1}" for i in range(n_samples)],
        "Condition": np.random.choice(bios, size=n_samples, replace=True),
        "Batch": np.random.choice(batches, size=n_samples, replace=True)
    })

    # Simulation settings per feature
    r = np.random.uniform(1.0, 3.0, size=n_features) # Dispersion
    z_target = np.random.uniform(0.1, 0.5, n_features)  # e.g. 20–50% zeros

    # Baseline log-abundance and true effects
    baseline_log = np.random.normal(loc=2, scale=1, size=n_features)

    # compute per‐feature NB zero probability
    mu = np.exp(baseline_log)
    p  = r / (r + mu)
    nb_zero = p**r

    # invert for p_zero
    p_zero = (z_target - nb_zero) / (1 - nb_zero)
    p_zero = np.clip(p_zero, 0, 1)

    # Biological effect
    effect_sizes = np.zeros(n_features)
    effect_idx = np.random.choice(n_features, n_diff, replace = False)
    effect_sizes[effect_idx] = np.random.normal(loc=2.0, scale = 4.0, size=n_diff)

    # Batch effect
    batch_sizes = np.zeros(n_features)
    batch_idx = np.random.choice(n_features, b_diff, replace = False)
    batch_sizes[batch_idx] = np.random.normal(loc=1.0, scale = 2.0, size=b_diff)

    # Simulating counts without biological effect
    counts = np.zeros((len(metadata), n_features), dtype=int)
    counts_batch = np.zeros((len(metadata), n_features), dtype=int)
    for i, row in metadata.iterrows():
        mu = baseline_log
        mu_batch = mu + (batch_sizes if row["Batch"]==batches[1] else 0) # Batch shift on Batch 2
        p = r / (r + np.exp(mu))
        p_batch = r / (r + np.exp(mu_batch))
        is_zero = np.random.binomial(1, p_zero)
        counts_i = nbinom(r, p).rvs()
        counts[i, :] = np.where(is_zero==1, 0, counts_i)
        counts_i_batch = nbinom(r, p_batch).rvs()
        counts_batch[i, :] = np.where(is_zero==1, 0, counts_i_batch)
    
    # Case 1: No batch, no bio
    count_matrix_no_bt = pd.DataFrame(counts, columns = [f"OTU{j+1}" for j in range(n_features)])
    count_matrix_no_bt = pd.concat([metadata, count_matrix_no_bt], axis = 1)
    # Case 2: Batch, no bio
    count_matrix_no_t = pd.DataFrame(counts_batch, columns = [f"OTU{j+1}" for j in range(n_features)])
    count_matrix_no_t = pd.concat([metadata, count_matrix_no_t], axis = 1)

    sim_data_no_bt.append(count_matrix_no_bt)
    sim_data_no_t.append(count_matrix_no_t)
    
    # Simulating counts with biological effect
    counts = np.zeros((len(metadata), n_features), dtype=int)
    counts_batch = np.zeros((len(metadata), n_features), dtype=int)
    for i, row in metadata.iterrows():
        mu = baseline_log + (effect_sizes if row["Condition"]==bios[1] else 0) # Biological shift on group B
        mu_batch = mu + (batch_sizes if row["Batch"]==batches[1] else 0) # Batch shift on Batch 2
        p = r / (r + np.exp(mu))
        p_batch = r / (r + np.exp(mu_batch))
        is_zero = np.random.binomial(1, p_zero)
        counts_i = nbinom(r, p).rvs()
        counts[i, :] = np.where(is_zero==1, 0, counts_i)
        counts_i_batch = nbinom(r, p_batch).rvs()
        counts_batch[i, :] = np.where(is_zero==1, 0, counts_i_batch)
    
    # Case 3: No batch, bio
    count_matrix_no_b = pd.DataFrame(counts, columns = [f"OTU{j+1}" for j in range(n_features)])
    count_matrix_no_b = pd.concat([metadata, count_matrix_no_b], axis = 1)
    # Case 4: Batch, bio
    count_matrix_bt = pd.DataFrame(counts_batch, columns = [f"OTU{j+1}" for j in range(n_features)])
    count_matrix_bt = pd.concat([metadata, count_matrix_bt], axis = 1)

    sim_data_no_b.append(count_matrix_no_b)
    sim_data_bt.append(count_matrix_bt)

In [4]:
plotPCoA(sim_data_bt[0], sample_label="SampleID", batch_label="Batch", experiment_label="Condition", method="aitchison")

### ABaCo runs

In [12]:
seed = 42
random.seed(seed)
np.random.seed(seed)
torch.manual_seed(seed)

if torch.cuda.is_available():
    torch.cuda.manual_seed_all(seed)

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

for i in range(1):

    df_no_bt = sim_data_no_bt[i]
    df_no_t = sim_data_no_t[i]
    df_no_b = sim_data_no_b[i]
    df_bt = sim_data_bt[i]

    # 1. Construct DataLoader object for ABaCo computation
    df_no_bt_dataloader = DataLoader(
        TensorDataset(
            torch.tensor(
                df_no_bt.select_dtypes(include="number").values, dtype=torch.float32
            ),  # samples
            one_hot_encoding(df_no_bt["Batch"])[0],  # one hot encoded batch information
            one_hot_encoding(df_no_bt["Condition"])[
                0
            ],  # one hot encoded biological information
        ),
        batch_size=1000,
    )
    df_no_t_dataloader = DataLoader(
        TensorDataset(
            torch.tensor(
                df_no_t.select_dtypes(include="number").values, dtype=torch.float32
            ),  # samples
            one_hot_encoding(df_no_t["Batch"])[0],  # one hot encoded batch information
            one_hot_encoding(df_no_t["Condition"])[
                0
            ],  # one hot encoded biological information
        ),
        batch_size=1000,
    )
    df_no_b_dataloader = DataLoader(
        TensorDataset(
            torch.tensor(
                df_no_b.select_dtypes(include="number").values, dtype=torch.float32
            ),  # samples
            one_hot_encoding(df_no_b["Batch"])[0],  # one hot encoded batch information
            one_hot_encoding(df_no_b["Condition"])[
                0
            ],  # one hot encoded biological information
        ),
        batch_size=1000,
    )
    df_bt_dataloader = DataLoader(
        TensorDataset(
            torch.tensor(
                df_bt.select_dtypes(include="number").values, dtype=torch.float32
            ),  # samples
            one_hot_encoding(df_bt["Batch"])[0],  # one hot encoded batch information
            one_hot_encoding(df_bt["Condition"])[
                0
            ],  # one hot encoded biological information
        ),
        batch_size=1000,
    )

    # 2. Run ABaCo on datasets
    # abaco_no_bt = abaco_run(
    #     dataloader=df_no_bt_dataloader,
    #     prior="Normal",
    #     n_batches=2,
    #     n_bios=2,
    #     input_size=n_features,
    #     device=device,
    #     w_contra=1.0,  # Modifiable, rather keep it on 100 as baseline
    #     kl_cycle=False,
    #     w_cycle=1e-4,
    #     seed=None,
    #     smooth_annealing=True,
    #     pre_epochs=4000,
    #     post_epochs=4000,
    #     vae_post_lr=1e-4,
    #     adv_lr=1e-6,
    #     disc_lr=1e-6,
    # )
    # abaco_no_t = abaco_run(
    #     dataloader=df_no_t_dataloader,
    #     prior="Normal",
    #     n_batches=2,
    #     n_bios=2,
    #     input_size=n_features,
    #     device=device,
    #     w_contra=1.0,  # Modifiable, rather keep it on 100 as baseline
    #     kl_cycle=False,
    #     w_cycle=1e-4,
    #     seed=None,
    #     smooth_annealing=True,
    #     pre_epochs=4000,
    #     post_epochs=4000,
    #     vae_post_lr=2e-4,
    #     adv_lr=1e-4,
    #     disc_lr=1e-4,
    # )
    # abaco_no_b = abaco_run(
    #     dataloader=df_no_b_dataloader,
    #     prior="VMM",
    #     n_batches=2,
    #     n_bios=2,
    #     input_size=n_features,
    #     device=device,
    #     w_contra=100.0,  # Modifiable, rather keep it on 100 as baseline
    #     kl_cycle=False,
    #     w_cycle=1e-4,
    #     seed=None,
    #     smooth_annealing=True,
    #     pre_epochs=4000,
    #     post_epochs=4000,
    #     vae_post_lr=1e-4,
    #     adv_lr=1e-6,
    #     disc_lr=1e-6,
    # )
    abaco_bt = abaco_run(
        dataloader=df_bt_dataloader,
        n_batches=2,
        n_bios=2,
        input_size=n_features,
        device=device,
        prior = "VMM", # Prior distribution used (it can be also "MoG" or "Std"). Baseline is "VMM" which stands for VampPrior Mixture Model
        w_contra=1000.0,  # Contrastive learning power: higher value yields a higher separation of biological groups at the latent space. Sometimes higher is better.
        beta=100.0,  # KL-divergence coefficient: higher value yields bigger penalization from the prior distribution
        kl_cycle=False,  # Regularization term used during the batch correction (ABaCo second phase)
        seed=None,
        smooth_annealing=True,  # Slow batch masking during ABaCo second phase to avoid exploding gradients
        pre_epochs=5000,  # ABaCo first phase epochs: data reconstruction
        post_epochs=2500,  # ABaCo second phase epohcs: batch correction
        vae_pre_lr=2e-4,
        vae_post_lr=2e-4,
        adv_lr=1e-5,  # Adversarial learning rate: to the encoder, if batch effect is on latent space
        disc_lr=1e-5,  # Discriminator learning rate: to the batch discriminator
        new_pre_train=False,  # Another config
        w_cycle=1e-3,  # Higher value lets to more unstability during ABaCo second phase
    )

    # 3. Reconstruct data with trained ABaCo models
    # no_bt_recon_data = abaco_recon(
    #     model=abaco_no_bt,
    #     device=device,
    #     data=df_no_bt,
    #     dataloader=df_no_bt_dataloader,
    #     sample_label="SampleID",
    #     batch_label="Batch",
    #     bio_label="Condition",
    #     seed=None,
    #     monte_carlo=1,
    # )
    # no_t_recon_data = abaco_recon(
    #     model=abaco_no_t,
    #     device=device,
    #     data=df_no_t,
    #     dataloader=df_no_t_dataloader,
    #     sample_label="SampleID",
    #     batch_label="Batch",
    #     bio_label="Condition",
    #     seed=None,
    #     monte_carlo=1,
    # )
    # no_b_recon_data = abaco_recon(
    #     model=abaco_no_b,
    #     device=device,
    #     data=df_no_b,
    #     dataloader=df_no_b_dataloader,
    #     sample_label="SampleID",
    #     batch_label="Batch",
    #     bio_label="Condition",
    #     seed=None,
    #     monte_carlo=1,
    # )
    bt_recon_data = abaco_recon(
        model=abaco_bt,
        device=device,
        data=df_bt,
        dataloader=df_bt_dataloader,
        sample_label="SampleID",
        batch_label="Batch",
        bio_label="Condition",
        seed=None,
        monte_carlo=1,
    )

Pre-training: VAE for reconstructing data and batch mixing adversarial training:   0%|          | 0/5000 [00:00<?, ?it/s, adv=-3921.9746, contra=6896.3647, disc=37348.2891, elbo=1561827.2500, epoch=0/5001]

Pre-training: VAE for reconstructing data and batch mixing adversarial training: 100%|██████████| 5000/5000 [01:30<00:00, 54.96it/s, adv=-21.1220, contra=4135.3149, disc=33.5780, elbo=9326.2363, epoch=4999/5001]        
Training: VAE decoder with masked batch labels: 100%|██████████| 2500/2500 [00:30<00:00, 82.12it/s, epoch=2500/2500, vae_loss=275.0088]


In [13]:
ohe_batch = one_hot_encoding(df_bt["Condition"])[0]

# Get PCA of posterior distribution
z_pca = []
data_iter = iter(df_bt_dataloader)
        
for loader_data in data_iter:
    x = loader_data[0].to(device)
    y = loader_data[1].to(device).float()  # Batch label
    pca = abaco_bt.pca_posterior(torch.cat([x, y], dim=1))
    z_pca.append(pca)

# Plot PCA from sample
z_stacked = np.vstack(z_pca)

# Sample from prior distribtution for countour plot
prior_sample = abaco_bt.pca_prior(n_samples=1000)

# scatter = plt.scatter(z_stacked[:, 0], z_stacked[:, 1], c=torch.cat(labels).numpy(), cmap='tab10', alpha=0.7)
# cbar = plt.colorbar(scatter, boundaries = np.arange(11)-0.5)
# cbar.set_ticks(np.arange(10))
# cbar.set_ticklabels(np.arange(10))
# cbar.set_label('Label')

# Plot posterior into prior contour surface plot

plt.figure(figsize=(8, 8))
contour = contour_plot(prior_sample, n_levels=10, x_offset=5, y_offset=5, alpha=1)
scatter = plt.scatter(
    z_stacked[:, 0],
    z_stacked[:, 1],
    alpha=1,
    c=ohe_batch.detach().cpu().numpy().argmax(axis=1),
    cmap="Paired",
    s=8,
)

# plt.xlim([-20, 30])
# plt.ylim([-10, 10])

plt.show()

In [14]:
plotPCoA(bt_recon_data, sample_label="SampleID", batch_label="Batch", experiment_label="Condition")

#### PERMANOVA function

In [11]:
def explained_var(df):
    """
    Computes PERMANOVA for batch and biological grouping and returns R^2 value (explained variance of grouping label)
    """
    df = DataTransform(df, factors = ["SampleID", "Batch", "Condition"], count=True)
    metadata = df[['SampleID','Condition','Batch']].set_index('SampleID')
    feature_data = df.drop(columns=['SampleID','Condition','Batch'])

    # Compute Aitchison distance
    dist_array = pdist(feature_data.values, metric='euclidean')
    dm = DistanceMatrix(squareform(dist_array), ids=metadata.index.tolist())

    # PERMANOVA for Condition
    res_c = permanova(dm, grouping=metadata['Condition'], permutations=999)
    # PERMANOVA for Batch
    res_b = permanova(dm, grouping=metadata['Batch'], permutations=999)

    # Extract parameters for R2 calculation
    N = int(res_c['sample size'])
    g_c = int(res_c['number of groups'])
    g_b = int(res_b['number of groups'])
    F_c = float(res_c['test statistic'])
    F_b = float(res_b['test statistic'])

    dfB_c, dfW_c = g_c - 1, N - g_c
    dfB_b, dfW_b = g_b - 1, N - g_b

    # Compute R2
    r2_c = (F_c * dfB_c) / (F_c * dfB_c + dfW_c)
    r2_b = (F_b * dfB_b) / (F_b * dfB_b + dfW_b)

    return r2_c, r2_b

#### R^2 computation

In [33]:
# Plot boxplot for explained variance
r2_results_no_bt = []
r2_results_no_t = []
r2_results_no_b = []
r2_results_bt = []

for i in range(sims):
    # No batch, no biology
    r2_c, r2_b = explained_var(sim_data_no_bt[i])
    r2_results_no_bt.append({'Condition_R2': r2_c, 'Batch_R2': r2_b})
    # Batch, no biology
    r2_c, r2_b = explained_var(sim_data_no_t[i])
    r2_results_no_t.append({'Condition_R2': r2_c, 'Batch_R2': r2_b})
    # No batch, biology
    r2_c, r2_b = explained_var(sim_data_no_b[i])
    r2_results_no_b.append({'Condition_R2': r2_c, 'Batch_R2': r2_b})
    # Batch, biology
    r2_c, r2_b = explained_var(sim_data_bt[i])
    r2_results_bt.append({'Condition_R2': r2_c, 'Batch_R2': r2_b})

# Compile all runs
df_r2_all_no_bt = pd.DataFrame(r2_results_no_bt)
df_r2_all_no_t = pd.DataFrame(r2_results_no_t)
df_r2_all_no_b = pd.DataFrame(r2_results_no_b)
df_r2_all_bt = pd.DataFrame(r2_results_bt)

#### Batch correction using ABaCo

In [37]:
abaco_no_bt = []
abaco_no_b = []
abaco_no_t = []
abaco_bt = []

folder = "simulated/ABaCo"

for filename in os.listdir(folder):
    if os.path.isfile(os.path.join(folder, filename)) and filename.startswith("data_no_bt"):
            abaco_no_bt.append(os.path.join(folder, filename))
    
    elif os.path.isfile(os.path.join(folder, filename)) and filename.startswith("data_no_t"):
            abaco_no_t.append(os.path.join(folder, filename))
    
    elif os.path.isfile(os.path.join(folder, filename)) and filename.startswith("data_no_b"):
            abaco_no_b.append(os.path.join(folder, filename))
    
    elif os.path.isfile(os.path.join(folder, filename)) and filename.startswith("data_bt"):
            abaco_bt.append(os.path.join(folder, filename))

In [6]:
# Plot boxplot for explained variance
abaco_r2_results_no_bt = []
abaco_r2_results_no_t = []
abaco_r2_results_no_b = []
abaco_r2_results_bt = []

for i in range(50):
    # No batch, no biology
    r2_c, r2_b = explained_var(DataPreprocess(abaco_no_bt[i], factors=["SampleID", "Batch", "Condition"]))
    abaco_r2_results_no_bt.append({'Condition_R2': r2_c, 'Batch_R2': r2_b})
    # Batch, no biology
    r2_c, r2_b = explained_var(DataPreprocess(abaco_no_t[i], factors=["SampleID", "Batch", "Condition"]))
    abaco_r2_results_no_t.append({'Condition_R2': r2_c, 'Batch_R2': r2_b})
    # No batch, biology
    r2_c, r2_b = explained_var(DataPreprocess(abaco_no_b[i], factors=["SampleID", "Batch", "Condition"]))
    abaco_r2_results_no_b.append({'Condition_R2': r2_c, 'Batch_R2': r2_b})
    # Batch, biology
    r2_c, r2_b = explained_var(DataPreprocess(abaco_bt[i], factors=["SampleID", "Batch", "Condition"]))
    abaco_r2_results_bt.append({'Condition_R2': r2_c, 'Batch_R2': r2_b})

# Compile all runs
df_abaco_r2_all_no_bt = pd.DataFrame(abaco_r2_results_no_bt)
df_abaco_r2_all_no_t = pd.DataFrame(abaco_r2_results_no_t)
df_abaco_r2_all_no_b = pd.DataFrame(abaco_r2_results_no_b)
df_abaco_r2_all_bt = pd.DataFrame(abaco_r2_results_bt)

In [34]:
# Boxplot of R2
fig, axes = plt.subplots(4, 3, figsize = (20, 15))

# Original state of each group
df_r2_all_no_bt.boxplot(showfliers = False, ax=axes[0][0])
axes[0][0].set_ylim([0, 1])

df_r2_all_no_t.boxplot(showfliers = False, ax=axes[1][0])
axes[1][0].set_ylim([0, 1])

df_r2_all_no_b.boxplot(showfliers = False, ax=axes[2][0])
axes[2][0].set_ylim([0, 1])

df_r2_all_bt.boxplot(showfliers = False, ax=axes[3][0])
axes[3][0].set_ylim([0, 1])

# Ground truth
df_r2_all_no_bt.boxplot(showfliers = False, ax=axes[0][1])
axes[0][1].set_ylim([0, 1])

df_r2_all_no_bt.boxplot(showfliers = False, ax=axes[1][1])
axes[1][1].set_ylim([0, 1])

df_r2_all_no_b.boxplot(showfliers = False, ax=axes[2][1])
axes[2][1].set_ylim([0, 1])

df_r2_all_no_b.boxplot(showfliers = False, ax=axes[3][1])
axes[3][1].set_ylim([0, 1])

# ABaCo results
df_abaco_r2_all_no_bt.boxplot(showfliers = False, ax=axes[0][2])
axes[0][2].set_ylim([0, 1])

df_abaco_r2_all_no_t.boxplot(showfliers = False, ax=axes[1][2])
axes[1][2].set_ylim([0, 1])

df_abaco_r2_all_no_b.boxplot(showfliers = False, ax=axes[2][2])
axes[2][2].set_ylim([0, 1])

df_abaco_r2_all_bt.boxplot(showfliers = False, ax=axes[3][2])
axes[3][2].set_ylim([0, 1])

axes[0, 0].set_title('Simulated data')
axes[0, 1].set_title('Ground-truth data')
axes[0, 2].set_title('ABaCo')

axes[0, 0].set_ylabel('Baseline data')
axes[1, 0].set_ylabel('Data with batch effect')
axes[2, 0].set_ylabel('Data with biological differences')
axes[3, 0].set_ylabel('Data with biological and batch effect')

fig.suptitle("Explained variance simulated data distribution by group", fontsize=16)
plt.show()

NameError: name 'df_abaco_r2_all_no_bt' is not defined